In [1]:
from skewPy import SkewT
import matplotlib.pyplot as plt

plt.close('all')

S1 = SkewT.Sounding(filename='Palau_test_sndg.txt', fmt='PALAU', date_to_read = 0)
#S1 = SkewT.Sounding(data={}, fmt='PISTON_EDT')
#S1.make_skewt_axes()
#S2 = SkewT.Sounding(data={}, fmt='PISTON_EDT')
#S1.readfile('/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180820_2335.txt')
#data1 = S1.data
#S1.add_profile()
#S1.add_profile(color='r', bloc=0.5, bcol='r')
#S1.readfile('/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180821_0530.txt')
#S1.add_profile(color='b', bloc=1, bcol='b')
#S1.readfile('/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180821_1235.txt')
#S1.add_profile(color='g', bloc=1.5, bcol='g')
#fig.set_title('test')
# Issue might be with fact that changed way of indexing which sounding in the file is read
#S['temp'][SkewT.tropopause_index(S['temp'])]

TabError: inconsistent use of tabs and spaces in indentation (SkewT.py, line 518)

In [2]:
S1.cape()

(2008.5271719218913,
 masked,
 '2015-05-01_00:00:00',
 25.175429375588038,
 77.171938831259695,
 0.019325997405940966,
 masked_array(data = [0.018422604503309237 0.018556361035867663 0.01901389680339424
  0.019338630270288936],
              mask = [False False False False],
        fill_value = -999.0))

In [12]:
from datetime import datetime
import numpy as np
from numpy import ma,array,linspace,log,cos,sin,pi,zeros,exp,arange,interp,flipud
import matplotlib.pyplot as plt

# Finds the name of the file, opens it, reads the lines
fname = 'Palau_test_sndg.txt'
fid = open(fname)
lines = fid.readlines()
nlines = len(lines) # number of lines
ndata = nlines-34 # number of lines of data; will need to change for Palau soundings
output = {} #This will be the dictionary that comes out

# Pulls some info re the data and units
fields = lines[7].split() # pulls the names of the fields
units = lines[8].split() # pulls the units of the above fields
print('fields = ', fields)
print('units = ', units)

# Pulls the header locations, index, and lists them
ndates = 0
header_list = np.empty(0)
header_index = np.empty(0, dtype=int) 
for i in range(len(lines)):
    if lines[i].startswith('91408'):
        header_list = np.append(header_list, lines[i])
        header_index = np.append(header_index, i)
        ndates += 1
        
#print(ndates)
#print(header_index)
#print(header_list)


# Loops through each header and pulls the data
for i in header_index:
    header = lines[i]
    #print(header) 

    # Not applicable here, will need to comment out or adapt
    if header[:] == '00000':
    # WRF profile
        station = '-99999'
        lon = float(header.split()[5].strip(","))
        lat = float(header.split()[6])
        sounding_date = header.split()[-1]
        print(lon)

    # Pulls station name and date from header
    else:

        station = header[:5]
        #print('station = ', station); print()
        dstr = (' ').join(header.split()[-4:])
        sounding_date = datetime.strptime(dstr, "%HZ %d %b %Y").strftime("%Y-%m-%d_%H:%M:%S") 
        #print('date = ', sounding_date); print()


# Fills an array; 999 will be default "NaN" value
for ff in fields:
    output[ff.lower()]=zeros((nlines-34, 62))  - 999.
#print('output is ', output); print()

# Sets up arrays for indexing the data; might will need to change. These determine where each field is
lhi=[1, 9,16,23,30,37,46,53,58,65,71]
rhi=[7,14,21,28,35,42,49,56,63,70,77]


lcounter = 0 # counts number of lines
ldata = 0 # counts amount of data
dat_col = 0 # used to determin column of data
data_end = 999 # toggle whether to read new data or now

for line,idx in zip(lines[:],range(len(lines))):
    lcounter += 1
    try: 
        output[fields[0].lower()][idx, dat_col] = float(line[lhi[0]:rhi[0]])
        ldata += 1
        data_end = 0
    except ValueError: 
        if data_end == 0:
        #print('break read')
            dat_col +=1 
        data_end = 1
        #print(dat_col)
        pass

#print(lcounter)
#print(ldata)



for ii in range(1, len(rhi)):
    lcounter = 0 # counts number of lines
    ldata = 0 # counts amount of data
    dat_col = 0 # used to determine column of data
    data_end = 999 # toggle whether to read new columb date or not
    tog_read = 999 # toggles whether we are in the body of the main data to read or not
        
    for line,idx in zip(lines[:],range(len(lines))):
        lcounter += 1
        # waits until we are in the body of the main data to start reading
        if line.startswith('91408 PTRO Koror'):
            tog_read = 1 #go ahead and starts reading
            #print('read go')
            
        # if reach the end of a block, turn off reading
        if line.startswith('Station information'):
            tog_read = 0 # don't read anymore
            dat_col +=1 
            #print('read stop')
            
        # if in the body of the sounding, read the data
        if tog_read == 1:
            try: 
                #print(float(line[lhi[ii]:rhi[ii]]))
                output[fields[ii].lower()][idx, dat_col] = float(line[lhi[ii]:rhi[ii]].strip())
                ldata += 1
                data_end = 1
            except ValueError: 
                #if data_end == 1:
                #    print('break read')
                #    
                #data_end = 0
                #print(dat_col)
                pass
        # if not, don't read the data
        else:
            #print('not reading')
            pass


data = {}
for field in fields:
    ff=field.lower()
    data[ff]=ma.masked_values(output[ff][:,0], -999.)

print(data['pres'])


fields =  ['PRES', 'HGHT', 'TEMP', 'DWPT', 'RELH', 'MIXR', 'DRCT', 'SKNT', 'THTA', 'THTE', 'THTV']
units =  ['hPa', 'm', 'C', 'C', '%', 'g/kg', 'deg', 'knot', 'K', 'K', 'K']
[-- -- -- ..., -- -- --]


In [13]:
data.keys()

dict_keys(['pres', 'hght', 'temp', 'dwpt', 'relh', 'mixr', 'drct', 'sknt', 'thta', 'thte', 'thtv'])

In [3]:
test = {'hello':''}
print(test)

{'hello': ''}


In [13]:
test.keys() == {}.keys()

False

In [32]:
print()

dict_keys(['hello'])


In [37]:
dict?